In [1]:
import pandas as pd
import numpy as np
import json
import datetime
import random

In [2]:
with open("superedge_locations_dates.json", 'r') as f:
    dates = json.load(f)

In [3]:
def time_converter(time_stamp):
    normalizer = 1000;
    return datetime.datetime.fromtimestamp(time_stamp/normalizer).strftime('%Y')

In [4]:
new_dates = {k: time_converter(v) for k, v in dates['publicationDate'].items()}

The list of tuples show the whole range od years that our dataset span togeather with the total number of news in each year


In [5]:
count_dict = dict()
for i in new_dates:
    year = new_dates[i]
    if year in count_dict:
        count_dict[year] += 1
    else:
        count_dict[year] = 1
print(sorted(count_dict.items(),reverse=True))

[('2017', 135), ('2016', 331), ('2015', 492), ('2014', 461), ('2013', 336), ('2012', 331), ('2011', 444), ('2010', 504), ('2009', 635), ('2008', 634), ('2007', 577), ('2006', 607), ('2005', 490), ('2004', 462), ('2003', 547), ('2002', 932), ('2001', 710), ('2000', 838), ('1999', 950), ('1998', 873), ('1997', 726), ('1996', 423), ('1995', 544), ('1994', 533), ('1993', 475), ('1992', 613), ('1991', 181), ('1990', 232), ('1989', 237), ('1988', 223), ('1987', 265), ('1986', 299), ('1985', 200), ('1984', 218), ('1983', 187), ('1982', 140), ('1981', 127), ('1980', 142), ('1979', 103), ('1978', 94), ('1977', 78), ('1976', 108), ('1975', 149), ('1974', 132), ('1973', 201), ('1972', 194), ('1971', 135), ('1970', 142), ('1969', 97), ('1968', 108), ('1967', 240), ('1966', 399), ('1965', 349), ('1964', 310), ('1963', 250), ('1962', 167), ('1961', 157), ('1960', 151), ('1959', 191), ('1958', 180), ('1957', 126), ('1956', 206), ('1955', 191), ('1954', 418), ('1953', 302), ('1952', 207), ('1951', 219

In [6]:
with open("superedge_locations.json", 'r') as f:
    connections = json.load(f)

In [7]:
with open("newloc2coord.json", 'r') as f:
    standart_names = json.load(f)

In [8]:
canton_names = list()
for row in pd.read_json("ch.json")['features']:
    canton_names.append(row['properties']['name'])

Now we standardize the names of locations 

In [9]:
standartized_connections = dict()
for i  in connections:
    try:
        standartized_connections[i] = [standart_names[loc] for loc in connections[i]]
    except:
        pass

In [10]:
coonections_w_dates = dict()
for k,v in standartized_connections.items():
    connect_list = []
    for loc in v:
        if loc !=None and loc in canton_names and loc not in connect_list :
            connect_list.append(loc)
    coonections_w_dates[k] = (connect_list,new_dates[k])

In [11]:
cleaned_connections = dict()
for l in standartized_connections.values():
    for loc in l:
        if loc:
            cleaned_connections[loc] = dict()

for year in count_dict:
    for loc in cleaned_connections:
        cleaned_connections[loc][year] = list()

In [12]:
for k in coonections_w_dates:
    connections = coonections_w_dates[k][0]
    year = coonections_w_dates[k][1]
    if len(connections) > 2:
        for loc in connections:
            cleaned_connections[loc][year].append({'id':k,'news':connections})

In [13]:
resulting_connections = dict()
for loc in cleaned_connections:
    if loc in canton_names:
        resulting_connections[loc] = cleaned_connections[loc]

Now we don't standardize the names of locations 

In [14]:
with open("superedge_locations.json", 'r') as f:
    connections = json.load(f)

In [15]:
with open("newloc2coord.json", 'r') as f:
    standart_names = json.load(f)

In [16]:
raw_connections = dict()
for i in connections:
    try:
        raw_connections[i] = [standart_names[loc] for loc in connections[i]]
        raw_connections[i] = [loc for loc in connections[i]]
    except:
        pass

In [17]:
raw_connections_w_date = dict()
for k,v in raw_connections.items():
    connect_list = []
    for loc in v:
        if loc.lower() != 'suisse' and loc !=None and standart_names[loc] in canton_names and loc not in connect_list:
            connect_list.append(loc)
    raw_connections_w_date[k] = (connect_list,new_dates[k])

In [18]:
connection_loc_year = dict()
seen_connection = dict()
for l in standartized_connections.values():
    for loc in l:
        if loc:
            connection_loc_year[loc] = dict()
            seen_connection[loc] = dict()

for year in count_dict:
    for loc in connection_loc_year:
        connection_loc_year[loc][year] = list()
        seen_connection[loc][year] = list()

In [19]:
for k in raw_connections_w_date:
    connections = raw_connections_w_date[k][0]
    year = coonections_w_dates[k][1]
    if len(connections) > 2:
        for loc in connections:
            if connections not in seen_connection[standart_names[loc]][year]:
                seen_connection[standart_names[loc]][year].append(connections)
                connection_loc_year[standart_names[loc]][year].append({'id':k,'news':connections})

In [20]:
resulting_connections = dict()
for loc in connection_loc_year:
    if loc in canton_names:
        resulting_connections[loc] = connection_loc_year[loc]

In [21]:
yearlyConnections = dict()
for year in count_dict:
    yearlyConnections[year] = set()
    
for canton in resulting_connections:
    for year in resulting_connections[canton]:
        n = 0
        for connection in resulting_connections[canton][year]:
            for loc in connection["news"]:
                # take one loc from each connection
                # if n > len(resulting_connections[canton][year]):
                #     break
                # else:
                #     n += 1
                yearlyConnections[year].add(loc)
                

for year in yearlyConnections:
    yearlyConnections[year] = list(yearlyConnections[year])

### `Canton Locations`

In [22]:
canton_coordinates = dict()
for canton in pd.read_json("ch.json")['features']:
    df = pd.DataFrame(canton['geometry']['coordinates'][0][0])
    canton_coordinates[canton['properties']['name']] = (df.mean(axis=0)[1].round(5), df.mean(axis=0)[0].round(5))

In [23]:
canton_coordinates['Aargau']

(47.392890000000001, 8.1405700000000003)

### Excerpts

In [24]:
with open("excerpts_filtered.json", 'r') as f:
    exerpts = json.load(f)

In [25]:
len(standartized_connections)

23148

In [26]:
exerpts_filtered = {k:exerpts[k] for k in standartized_connections.keys()}

In [27]:
len(exerpts_filtered)

23148

In [28]:
exerpts_filtered

{'28': {'alternativeExcerpt': '',
  'excerpt': "Le sport, ce ne sont pas que des hommes, des femmes, des résultats ou des statistiques. Ce sont aussi des lieux. Certains ont marqué l'Histoire."},
 '30': {'alternativeExcerpt': '', 'excerpt': ''},
 '50': {'alternativeExcerpt': '',
  'excerpt': "Le sport, ce ne sont pas que des hommes, des femmes, des résultats ou des statistiques. Ce sont aussi des lieux. Certains ont marqué l'Histoire."},
 '89': {'alternativeExcerpt': '',
  'excerpt': "Maurice Tornay a brièvement évoqué à la radio Rhône FM  l'affaire  des problèmes fiscaux de Dominique Giroud, marchand de vin. Il s'est défendu de toute implication dans cette affaire de fraude fiscale.\r\n\r\n\r\n\r\n \r\n\r\n+ En direct par téléphone, Gaël Bourgeois, président du parti socialiste du Valais  romand."},
 '158': {'alternativeExcerpt': '',
  'excerpt': 'Reportage dans la classe de Noémie Chevalley, à l\'école de la Vignettaz, en ville de Fribourg, ainsi qu\'au CO de la Gruyère, à la Tour-de

In [289]:
df_filter = pd.read_csv("id_genre_theme_location_date.csv")

In [290]:
def split_to_list(row):
    return_list = list()
    for el in row.split(","):
        return_list.append(int(el.strip("[]")))
    return return_list

In [291]:
df_filter.genre_code = df_filter.genre_code.apply(lambda row: str(int(row.split(",")[0].strip("[]"))))   
df_filter.theme_code = df_filter.theme_code.apply(lambda row: str(int(row.split(",")[0].strip("[]"))))
df_filter.publicationDate = df_filter.publicationDate.apply(lambda row: str(int(row.split("/")[2])))
df_filter.loc_code = df_filter.loc_code.apply(split_to_list)
df_filter.id = df_filter.id.astype('str')

In [292]:
filtered_filter = df_filter[['id','genre_code','publicationDate']]

In [293]:
def get_connection(row):
    try: return connection_ref[row]
    except: return None

def get_canton(row):
    try: return canton_ref[row]
    except: return None

filtered_filter['connections'] = filtered_filter.id.apply(get_connection)
filtered_filter['canton'] = filtered_filter.id.apply(get_canton)
filtered_filter = filtered_filter.dropna()

/usr/local/lib/python3.6/site-packages/ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


In [294]:
resulting_connection_filter = dict()
for genre in filtered_filter.genre_code.unique():
    resulting_connection_filter[genre] = dict()
    for canton in canton_names:
        resulting_connection_filter[genre][canton] = dict()
        for year in filtered_filter.publicationDate.unique():
            resulting_connection_filter[genre][canton][year] = list()

In [295]:
for _, row in filtered_filter.iterrows():
    for canton in row.canton:
        resulting_connection_filter[row.genre_code][canton][row.publicationDate].append(row.connections)

In [299]:
resulting_connection_filter["259"]

{'Aargau': {'1937': [],
  '1938': [],
  '1939': [],
  '1940': [],
  '1941': [],
  '1942': [],
  '1943': [],
  '1944': [],
  '1945': [],
  '1946': [],
  '1949': [],
  '1950': [],
  '1951': [],
  '1952': [],
  '1953': [],
  '1954': [],
  '1955': [],
  '1956': [],
  '1957': [],
  '1958': [],
  '1959': [],
  '1960': [],
  '1961': [],
  '1962': [],
  '1963': [],
  '1964': [],
  '1965': [],
  '1966': [],
  '1967': [],
  '1968': [],
  '1969': [],
  '1970': [],
  '1971': [],
  '1972': [],
  '1973': [],
  '1974': [],
  '1975': [],
  '1976': [],
  '1977': [],
  '1978': [],
  '1979': [],
  '1980': [],
  '1981': [],
  '1982': [],
  '1983': [],
  '1984': [],
  '1985': [],
  '1986': [],
  '1987': [],
  '1988': [],
  '1989': [],
  '1990': [],
  '1991': [],
  '1992': [],
  '1993': [],
  '1994': [],
  '1995': [],
  '1996': [],
  '1997': [],
  '1998': [],
  '1999': [],
  '2000': [],
  '2001': [],
  '2002': [],
  '2003': [],
  '2004': [],
  '2005': [],
  '2006': [],
  '2007': [],
  '2008': [],
  '2009': 

In [296]:
# SAVE 
with open('canton_filter_connections.js', 'w') as outfile:
    json.dump(resulting_connection_filter, outfile, ensure_ascii=False)

In [255]:
filtered_filter = filtered_filter.dropna()

id  genre_code  publicationDate  \
3           28         273             2013   
75         158         273             2013   
173        347         273             2013   
482        926         208             2013   
720       1390         273             2013   
760       1466        -100             2013   
817       1580         273             2013   
879       1710         273             2013   
904       1744         259             2013   
1066      2038         133             2013   
1079      2069         273             2013   
1118      2145         273             2013   
1159      2219         218             2013   
1163      2225         273             2013   
1234      2346         273             2013   
1249      2377         273             2013   
1390      2677         273             2013   
1400      2692         273             2013   
1452      2820         273             2013   
1537      2991         273             2013   
1601      3138         273             2013   
1631      3184         273             2013   
1664      3248         273             2013   
1668      3258         273             2013   
1696      3313         273             2013   
1742      3410         273             2013   
1754      3434         259             2013   
1792      3500         218             2013   
1795      3504         273             2013   
1801      3513         218             2013   
...        ...         ...              ...   
126638  369825         145             2004   
126650  369854         189             2004   
126651  369857         208             2004   
126676  369919         120             2004   
126761  370121         148             2004   
126876  370395         208             2004   
126877  370397         189             2004   
126931  370566         148             2004   
126948  370609         208             2004   
126957  370625         175             2004   
127014  370765         208             2004   
127074  370910         208             2004   
127075  370911         113             2004   
127181  371190         259             2004   
127263  371382         202             2004   
127266  371389         273             2004   
127285  371435         273             2004   
127297  371474         148             2004   
127339  371560         208             2004   
127383  371675         145             2004   
127564  372150         145             2004   
127580  372190         145             2004   
127585  372199         273             2004   
127633  372359         120             2004   
127666  372427         148             2004   
127674  372446         145             2004   
127680  372463         113             2004   
127743  372612         273             2004   
127765  372666         259             2004   
127803  372809         148             2004   

                                              connections  \
3       {'id': '28', 'news': ['Berne (canton)', 'Laube...   
75      {'id': '158', 'news': ['La Tour-de-Trême', 'Fr...   
173     {'id': '347', 'news': ['Jura (canton)', 'Berne...   
482     {'id': '926', 'news': ['COINTRIN', 'DUEBENDORF...   
720     {'id': '1390', 'news': ['Nendaz', 'Valais', 'E...   
760     {'id': '1466', 'news': ['Gruyères', 'Montbovon...   
817     {'id': '1580', 'news': ['Jura (canton)', 'jura...   
879     {'id': '1710', 'news': ['Posieux', 'Fribourg (...   
904     {'id': '1744', 'news': ['Berne (canton)', 'Fra...   
1066    {'id': '2038', 'news': ['Jura (canton)', 'Jura...   
1079    {'id': '2069', 'news': ['Lac de Neuchâtel', 'G...   
1118    {'id': '2145', 'news': ['Monte Verita', 'Ascon...   
1159    {'id': '2219', 'news': ['Berne (canton)', 'Jur...   
1163    {'id': '2225', 'news': ['Neuchâtel (canton)', ...   
1234    {'id': '2346', 'news': ['Lavaux', 'Vaud', 'Lau...   
1249    {'id': '2377', 'news': ['Suisse alémanique', '...   
1390    {'id': '2677', 'news': ['Valais', 'Vaud', 'Vil...   

In [211]:
filter_dict = dict()
for genre in publicationDate.genre_code.unique():
    filter_dict[genre] = dict()
    for year in publicationDate.publicationDate.unique():
        filter_dict[genre][year] = list()

In [212]:
for index, row in df_filter.iterrows():
    filter_dict[row.genre_code][row.publicationDate].append(str(row.id))

In [247]:
# IDs for Connections
connection_ref = dict()
canton_ref = dict()
for canton in resulting_connections:
    for year in resulting_connections[canton]:
        for connection in resulting_connections[canton][year]:
            connection_id = connection["id"]
            connection_ref[connection_id] = connection
            if connection_id in canton_ref:
                canton_ref[connection_id].append(canton)
            else:
                canton_ref[connection_id] = [canton]

In [214]:
resulting_dictionary_genres = dict()
for genre in df_filter.genre_code.unique():
    resulting_dictionary_genres[genre] = dict()
    for canton in canton_names:
        resulting_dictionary_genres[genre][canton] = dict()
        for year in df_filter.publicationDate.unique():
            resulting_dictionary_genres[genre][canton][year] = list()

In [221]:
import sys

In [224]:
for genre in filter_dict:
    for year in filter_dict[genre]:
        for news_id in filter_dict[genre][year]:
            try:
                connections,canton = connection_ref[news_id]
                resulting_dictionary_genres[genre][canton][year].append(connection)
            except:
                pass
                # print("Unexpected error:", sys.exc_info()[0])

In [220]:
resulting_dictionary_genres

{-100: {'Aargau': {1924: [],
   1928: [],
   1929: [],
   1930: [],
   1931: [],
   1932: [],
   1933: [],
   1934: [],
   1935: [],
   1936: [],
   1937: [],
   1938: [],
   1939: [],
   1940: [],
   1941: [],
   1942: [],
   1943: [],
   1944: [],
   1945: [],
   1946: [],
   1949: [],
   1950: [],
   1951: [],
   1952: [],
   1953: [],
   1954: [],
   1955: [],
   1956: [],
   1957: [],
   1958: [],
   1959: [],
   1960: [],
   1961: [],
   1962: [],
   1963: [],
   1964: [],
   1965: [],
   1966: [],
   1967: [],
   1968: [],
   1969: [],
   1970: [],
   1971: [],
   1972: [],
   1973: [],
   1974: [],
   1975: [],
   1976: [],
   1977: [],
   1978: [],
   1979: [],
   1980: [],
   1981: [],
   1982: [],
   1983: [],
   1984: [],
   1985: [],
   1986: [],
   1987: [],
   1988: [],
   1989: [],
   1990: [],
   1991: [],
   1992: [],
   1993: [],
   1994: [],
   1995: [],
   1996: [],
   1997: [],
   1998: [],
   1999: [],
   2000: [],
   2001: [],
   2002: [],
   2003: [],
   2004: 